In [1]:
#| include: false
# from nbdev.showdoc import *

In [2]:
#| export
import pathlib
import re
import rich
import numpy as np
import pandas as pd
import logging
from typing import Union

In [3]:
#| default_exp core

In [13]:
#| export
def extract_mertis_hk_columns(in_path):
    """
    Extracts column names from an MERTIS HK XML file.

    Args:
        in_path (pathlib.Path): Path to the input file.

    Returns:
        list: List of column names.
    """
    import xmltodict

    # Create the path to the XML file by appending '.xml' to the input path.
    in_file = in_path.with_suffix('.xml')

    # Open the XML file in read binary mode and parse it using xmltodict.
    with open(in_file, "rb") as f:
        obj = xmltodict.parse(f, xml_attribs=False)

    # Extract the column names from the parsed XML object.
    # The XML structure is assumed to be consistent with the provided example.
    return [x['name'] for x in obj['Product_Observational']['File_Area_Observational']['Table_Delimited']['Record_Delimited']['Field_Delimited']]


class MERTISDataPackReader:
    """
    Class to read and process MERTIS data.

    Attributes:
        input_dir (pathlib.Path): Input directory.
        output_dir (pathlib.Path): Output directory.
        log_level (str): Log level.
        fits_files (list): List of FITS files.
        input_path_dict (dict): Dictionary of input paths.
        collect_data (dict): Dictionary of collected data.
    """
    def __init__(self, input_dir, output_dir='', log_level=''):
        """
        Initialize the MERTISDataPackReader.

        Args:
            input_dir (str or pathlib.Path): Input directory.
            output_dir (str or pathlib.Path, optional): Output directory. Defaults to ''.
            log_level (str, optional): Log level. Defaults to ''.
        """
        self.input_dir = pathlib.Path(input_dir)
        self.output_dir = self.set_output_dir(output_dir)
        self.log_level = log_level
        self.log = self.set_logger()
        logging.info(f'{input_dir=}')
        self.fits_files = self.get_fits_files()
        self.input_path_dict = self.get_input_path_dict()

    def set_output_dir(self, output_dir):
        """
        Set the output directory.

        Args:
            output_dir (str or pathlib.Path): Output directory.

        Returns:
            pathlib.Path: Output directory.
        """
        if output_dir:
            return pathlib.Path(output_dir)
        else:
            return self.input_dir.parent / f'{self.input_dir.name}-analysis_products'

    def set_logger(self):
        """
        Set the logger.
        """
        log_level = 'WARNING' if not self.log_level else self.log_level
        logging.basicConfig(format='%(asctime)s|%(process)d|%(levelname)s|%(message)s',
                            level=logging.getLevelName(log_level))
        logger = logging.getLogger()
        return logger

    def get_fits_files(self):
        """
        Get the list of FITS files.

        Returns:
            list: List of FITS files.
        """
        return list(self.input_dir.glob('**/*tis*.fits')) + \
               [i for i in self.input_dir.glob('**/*_hk_*.dat') if 'tis' not in i.stem and 'tir' not in i.stem]

    def get_input_path_dict(self):
        """
        Get the dictionary of input paths.

        Returns:
            dict: Dictionary of input paths.
        """
        files_type = ['hk_default', 'hk_extended', 'sc_tis', 'sc_tir', 'sc_tis_ql', 'sc_tir_ql']
        return {
            ft: list(
                sorted(
                    filter(lambda x: ft in str(x.stem), self.fits_files),
                    key=lambda x: int(x.stem.split('_')[-1])
                )
            )
            for ft in files_type
        }

    def show_files(self):
        """
        Print statistics about the files in the input directory.

        Prints the number of files in the input directory and the number of files
        in the input directory that match the pattern '\d{8}_\d{8}'.
        """
        # Import the Counter class from the collections module.
        from collections import Counter
        # Compile a regular expression that matches the pattern '\d{8}_\d{8}'.
        regex = re.compile('\d{8}_\d{8}')

        # Print the number of files in the input directory.
        print('All files in input_dir :')
        # Count the number of files in the input directory.
        # The Counter class is used to count the occurrences of each file extension.
        rich.print(Counter([p.suffix for p in self.input_dir.rglob('*')]))

        # Print the number of files in the input directory matching the pattern '\d{8}_\d{8}'.
        print('All files in input_dir matching \d{8}:')
        # Count the number of files in the input directory that match the pattern '\d{8}_\d{8}'.
        # The regular expression is used to search for the pattern in the stem of each file path.
        # The Counter class is used to count the occurrences of each prefix before the pattern.
        rich.print(Counter([re.findall('^([^\d]*)_',p.stem)[0] for p in self.input_dir.rglob('*') if regex.search(p.stem)]))

    def filetypes2dict(self):
        """
        Convert the input files into a dictionary, where the keys are the file types and the values are lists of file paths.

        Returns:
            dict: A dictionary where the keys are the file types and the values are lists of file paths.
        """
        # Define the file types.
        files_type = ['hk_default', 'hk_extended', 'sc_tis', 'sc_tir', 'sc_tis_ql', 'sc_tir_ql']

        # Create a dictionary to store the file paths.
        input_path_dict = {}

        # Iterate over each file type.
        for ft in files_type:
            # Filter the fits files based on the file type.
            # Sort the filtered files based on the numeric part in the file name.
            # Convert the result to a list.
            input_path_dict[ft] = list(
                sorted(
                    filter(lambda x: ft in str(x.stem), self.fits_files),
                    key=lambda x: int(x.stem.split('_')[-1])
                )
            )

        # Return the dictionary.
        return input_path_dict

    def listfiletypes(self) :
        """
        Print the list of file types and the number of files for each file type.

        This function iterates over the input_path_dict dictionary and prints the file types and the number
        of files for each file type. The file types and the number of files are printed using the rich.print
        function.

        Returns:
            None
        """
        # Iterate over the input_path_dict dictionary and print the file types and the number of files for each file type.
        rich.print({k: [f.name for f in v] for k, v in self.input_path_dict.items()})
        
        # Print the number of files for each file type.
        rich.print({filetype:len(files_paths) for filetype,files_paths in self.input_path_dict.items()})
    
    def save_plot(self,
                  out_file,
                  dpi=150,
                  out_format='jpg'):
        """
        Save a plot to the output directory.

        Args:
            out_file (str): The name of the output file.
            dpi (int): The resolution of the saved image in dots per inch. Default is 150.
            out_format (str): The format of the saved image. Default is 'jpg'.

        Returns:
            None
        """
        # Construct the output file path by joining the output directory and the output file name.
        out_path = self.output_dir / (out_file +f'.{out_format}' )

        # Save the plot to the output file path with the specified resolution and format.
        plt.savefig(out_path,dpi=dpi)

        # Print a message indicating that the plot is being saved.
        print(f'Saving {out_path}')
        
    def data_collector(self):
        """
        Collect data from the input files and store it in the collect_data attribute.

        This function iterates over the input_path_dict dictionary, which contains the file paths for each file type.
        For each file type, it checks if there are files available and reads the data from the files.
        The collected data is stored in the collect_data attribute.

        Returns:
            None
        """
        from astropy.io import fits

        # Create an empty dictionary to store the collected data
        collect_data = {}

        # Iterate over the input_path_dict dictionary
        for filetype, files_paths in self.input_path_dict.items():

            # Check if the file type contains 'hk'
            if 'hk' in filetype:
                # Skip if there are no files
                if len(files_paths) == 0:
                    continue

                # Iterate over the files for the current file type
                for in_file in files_paths:
                    # Read the data from the file
                    data = pd.read_csv(in_file, names=extract_mertis_hk_columns(in_file))
                    print(f'Reading filetype: {filetype} from {in_file.stem}')

                    # Add the data to the collect_data dictionary
                    if filetype not in collect_data:
                        collect_data[filetype] = []
                    collect_data[filetype].append({
                        'data': data,
                        'path': in_file
                    })

            # Check if the file type contains 'sc_tis' or 'sc_tir'
            elif ('sc_tis' in filetype) or ('sc_tir' in filetype):
                # Remove the 'sc_' prefix from the file type
                filetype = re.sub('^sc_', '', filetype)

                # Skip if there are no files
                if len(files_paths) == 0:
                    continue

                # Iterate over the files for the current file type
                for in_file in files_paths:
                    # Read the data from the FITS file
                    hdulist = fits.open(str(in_file))
                    print(f'Reading filetype: {filetype} from {in_file.stem}')

                    # Add the data to the collect_data dictionary
                    if filetype not in collect_data:
                        collect_data[filetype] = []
                    collect_data[filetype].append({
                        'fits_data': hdulist,
                        'path': in_file
                    })

        # Store the collected data in the collect_data attribute
        self.collect_data = collect_data


    def data_assembler(self, verbose=False):
        """
        Assembles the collected data into convenient data structures.

        This function processes the collected data and stores it in convenient data structures. The processed data includes:
        - ``geom_ls``: a dictionary of dictionaries, where each dictionary contains the data for a specific file, and each inner dictionary contains the data for a specific parameter.
        - ``frames``: a dictionary of numpy arrays, where each array contains the data for a specific file.
        - ``wavelengths``: a dictionary of numpy arrays, where each array contains the wavelength data for a specific file.
        - ``mertis_tis_metadata``: a dictionary of pandas DataFrames, where each DataFrame contains the metadata for a specific file.
        - ``space_index``: a pandas Index object containing the indices of the space measurements.
        - ``bb7_index``: a pandas Index object containing the indices of the BB7 measurements.
        - ``bb3_index``: a pandas Index object containing the indices of the BB3 measurements.
        - ``planet_index``: a pandas Index object containing the indices of the planet measurements.
        """
        from astropy.table import Table, vstack
        from astropy.time import Time
        from rich.progress import track

        # call data_collector if no data loaded
        if not hasattr(self, 'collect_data'):
            self.data_collector()
            
        NODATA_GEOMETRY = -1.7976931348623157e+308 # min double, this is new
        
        # Initialize the data structures
        geom_ls = {}
        frames = {}
        wavelengths = {}
        mertis_tis_metadata = {}
        output_str = []
        
        # Iterate over the collected tis data
        for tis_data in track(self.collect_data["tis"],
                              total=len(self.collect_data["tis"]),
                              description="Loading files..."):
            if "table" not in tis_data["path"].name:
                # Read the data from the FITS file and convert it to a pandas DataFrame
                tmp_table = Table(tis_data["fits_data"][1].data).to_pandas()
                tmp_table['file'] = tis_data["path"].stem
                mertis_tis_metadata[tis_data["path"].stem] = tmp_table
                
                print(f'Reading filetype: tis from {tis_data["path"]}')
                # Convert the data to float64 to keep the native byteorder
                frames[tis_data["path"].stem] = tis_data["fits_data"]['MERTIS_TIS_CALIB_SCIENCE_DATA'].data.astype(np.float64)
                wavelengths[tis_data["path"].stem] = tis_data["fits_data"]['MERTIS_TIS_CALIB_SCIENCE_DATA_WAVELENGTH'].data.astype(np.float64) #-wav_correction_factor
                
                # Process the geometry data
                geom_ls[tis_data["path"].stem] = {k.name: k.data.astype(np.float64) for k in tis_data["fits_data"] if 'GEOM' in k.name}
                for geo_k, geo_v in geom_ls[tis_data["path"].stem].items():
                    geo_v[geo_v == NODATA_GEOMETRY] = np.nan
                geo_k = 'MERTIS_TIS_GEOMETRY_TARGET_LONGITUDE'
                output_str.append([tis_data["path"].stem, np.sum(np.isfinite(geo_v)), geo_v.size])
        
        # Preserve the original index in the source file
        mertis_tis_metadata_df = pd.concat(mertis_tis_metadata).reset_index(drop=False).drop(columns=['level_0']).rename(columns={"level_1": "file_index"})

        # Sort the metadata DataFrame by the TIME_UTC column
        mertis_tis_metadata_df_time_utc_sort_index = mertis_tis_metadata_df.sort_values('TIME_UTC').index.values
        mertis_tis_metadata_df = mertis_tis_metadata_df.sort_values('TIME_UTC').reset_index(drop=True)
        mertis_tis_metadata_df['TIME_UTC'] = pd.to_datetime(mertis_tis_metadata_df['TIME_UTC'], utc=True)


        # Identify the indices of the space, BB7, BB3, and planet measurements
        space_index = mertis_tis_metadata_df[mertis_tis_metadata_df['HK_STAT_TIS_DATA_ACQ_TARGET'].str.contains('Space')].index
        bb7_index = mertis_tis_metadata_df[mertis_tis_metadata_df['HK_STAT_TIS_DATA_ACQ_TARGET'].str.contains('BB7')].index
        bb3_index = mertis_tis_metadata_df[mertis_tis_metadata_df['HK_STAT_TIS_DATA_ACQ_TARGET'].str.contains('BB3')].index
        planet_index = mertis_tis_metadata_df[mertis_tis_metadata_df['HK_STAT_TIS_DATA_ACQ_TARGET'].str.contains('Planet')].index
        
        ########################################################################
        # generic wavelengths : not precise enough for scientific analysis!
        wav = wavelengths[list(wavelengths.keys())[-1]].mean(axis=1)
        n_wav = len(wav)
        n_corners = geom_ls[list(geom_ls.keys())[0]]['MERTIS_TIS_GEOMETRY_TARGET_LONGITUDE'].shape[0]
        
        # Print the output statistics
        if verbose:
            print(f'{n_wav=} # generic wavelengths : not precise enough for scientific analysis!')
            print(pd.DataFrame(columns=["tis_stem", "finite(geo)", "geo.size"], data=output_str).to_markdown())
            print("Indices of measurements targets (HK_STAT_TIS_DATA_ACQ_TARGET):")
            print(f'{space_index.shape=}')
            print(f'{bb7_index.shape=}')
            print(f'{bb3_index.shape=}')
            print(f'{planet_index.shape=}')
            # Print the collected data statistics
            print(f'Collected data statistics:')
            print(f'Number of TIS files: {len(self.collect_data.get("tis", []))}')
            print(f'Number of HK files: {len(self.collect_data.get("hk_default", [])) + len(self.collect_data.get("hk_extended", []))}')
            print(f'Number of TIR files: {len(self.collect_data.get("tir", []))}')
            print(f'Number of TIS QL files: {len(self.collect_data.get("tis_ql", []))}')
            print(f'Number of TIR QL files: {len(self.collect_data.get("tir_ql", []))}')
        # Store the processed data in the corresponding attributes
        self.geom_ls = geom_ls
        self.frames = frames
        self.wavelengths = wavelengths
        self.mertis_tis_metadata = mertis_tis_metadata         
        self.space_index = space_index
        self.bb7_index = bb7_index
        self.bb3_index = bb3_index
        self.planet_index = planet_index


In [ ]:

# class MERTISDataPackReader:
#     """
#     A class that reads session data from the MERTIS HK dataset.

#     Args:
#         input_dir (str or pathlib.Path): Input directory.
#         output_dir (str or pathlib.Path, optional): Output directory. Defaults to ''.
#         log_level (str, optional): Log level. Defaults to ''.

#     """
#     def __init__(self,
#                  input_dir: Union[str, pathlib.Path],
#                  output_dir: Union[str, pathlib.Path] = '',
#                  log_level: str = '') -> None:
#         """
#         Constructor method. Initializes the class.

#         Args:
#             input_dir (str or pathlib.Path): Input directory.
#             output_dir (str or pathlib.Path, optional): Output directory. Defaults to ''.
#             log_level (str, optional): Log level. Defaults to ''.

#         """
#         self.input_dir = pathlib.Path(input_dir)
#         print(f'{input_dir=}')
        
#         # set the logger
#         log_level = 'DEBUG' if not log_level else log_level
#         self.log_level = log_level
#         logging.basicConfig(format='|%(levelname)s|%(asctime)s|%(process)d|%(message)s',
#                             level= logging.getLevelName(log_level))
#         self.log = logging.getLogger()

In [ ]:
input_path = pathlib.Path('/home/kidpixo/Documents/programs_and_data/data/MERTIS/ESA/SGS/cruise_6/bc-mer-tm2raw-20240411T000000-20240412T000000-20240513T155530/cal/')
assert input_path.exists() == True
# list(input_path.glob('**/*tis*.fits'))
ms = MERTISDataPackReader(input_path,log_level='ERROR')
ms

In [7]:
logging.getLevelName(ms.log.level)

'ERROR'

In [8]:
ms.show_files()

All files in input_dir :


Counter({'.fits': 6, '.xml': 8, '.dat': 2})

All files in input_dir matching \d{8}:


Counter({'mer_cal_sc_tis_ql': 4, 'mer_cal_sc_tis': 8, 'mer_cal_hk_default': 2, 'mer_cal_hk_extended': 2})

In [9]:
ms.listfiletypes()

{
    'hk_default': ['mer_cal_hk_default_20240411_20240411.dat'],
    'hk_extended': ['mer_cal_hk_extended_20240411_20240411.dat'],
    'sc_tis': [
        'mer_cal_sc_tis_ql_20240411_20240411_1.fits',
        'mer_cal_sc_tis_20240411_20240411_1.fits',
        'mer_cal_sc_tis_ql_20240411_20240411_2.fits',
        'mer_cal_sc_tis_20240411_20240411_2.fits',
        'mer_cal_sc_tis_20240411_20240411_3.fits',
        'mer_cal_sc_tis_20240411_20240411_4.fits'
    ],
    'sc_tir': [],
    'sc_tis_ql': ['mer_cal_sc_tis_ql_20240411_20240411_1.fits', 'mer_cal_sc_tis_ql_20240411_20240411_2.fits'],
    'sc_tir_ql': []
}

{'hk_default': 1, 'hk_extended': 1, 'sc_tis': 6, 'sc_tir': 0, 'sc_tis_ql': 2, 'sc_tir_ql': 0}

In [10]:
ms.data_assembler()

Output()

Reading filetype: tis from 
/home/kidpixo/Documents/programs_and_data/data/MERTIS/ESA/SGS/cruise_6/bc-mer-tm2raw-20240411T000000-20240412T00000
0-20240513T155530/cal/mer_cal_sc_tis_ql_20240411_20240411_1.fits

Reading filetype: hk_default from mer_cal_hk_default_20240411_20240411
Reading filetype: hk_extended from mer_cal_hk_extended_20240411_20240411
Reading filetype: tis from mer_cal_sc_tis_ql_20240411_20240411_1
Reading filetype: tis from mer_cal_sc_tis_20240411_20240411_1
Reading filetype: tis from mer_cal_sc_tis_ql_20240411_20240411_2
Reading filetype: tis from mer_cal_sc_tis_20240411_20240411_2
Reading filetype: tis from mer_cal_sc_tis_20240411_20240411_3
Reading filetype: tis from mer_cal_sc_tis_20240411_20240411_4
Reading filetype: tis_ql from mer_cal_sc_tis_ql_20240411_20240411_1
Reading filetype: tis_ql from mer_cal_sc_tis_ql_20240411_20240411_2


Reading filetype: tis from 
/home/kidpixo/Documents/programs_and_data/data/MERTIS/ESA/SGS/cruise_6/bc-mer-tm2raw-20240411T000000-20240412T00000
0-20240513T155530/cal/mer_cal_sc_tis_20240411_20240411_1.fits

Reading filetype: tis from 
/home/kidpixo/Documents/programs_and_data/data/MERTIS/ESA/SGS/cruise_6/bc-mer-tm2raw-20240411T000000-20240412T00000
0-20240513T155530/cal/mer_cal_sc_tis_ql_20240411_20240411_2.fits

Reading filetype: tis from 
/home/kidpixo/Documents/programs_and_data/data/MERTIS/ESA/SGS/cruise_6/bc-mer-tm2raw-20240411T000000-20240412T00000
0-20240513T155530/cal/mer_cal_sc_tis_20240411_20240411_2.fits

Reading filetype: tis from 
/home/kidpixo/Documents/programs_and_data/data/MERTIS/ESA/SGS/cruise_6/bc-mer-tm2raw-20240411T000000-20240412T00000
0-20240513T155530/cal/mer_cal_sc_tis_20240411_20240411_3.fits

Reading filetype: tis from 
/home/kidpixo/Documents/programs_and_data/data/MERTIS/ESA/SGS/cruise_6/bc-mer-tm2raw-20240411T000000-20240412T00000
0-20240513T155530/cal/mer_cal_sc_tis_20240411_20240411_4.fits

|    | tis_stem                              |   finite(geo) |   geo.size |
|---:|:--------------------------------------|--------------:|-----------:|
|  0 | mer_cal_sc_tis_ql_20240411_20240411_1 |             0 |      28000 |
|  1 | mer_cal_sc_tis_20240411_20240411_1    |             0 |     862000 |
|  2 | mer_cal_sc_tis_ql_20240411_20240411_2 |             0 |      26000 |
|  3 | mer_cal_sc_tis_20240411_20240411_2    |             0 |     431000 |
|  4 | mer_cal_sc_tis_20240411_20240411_3    |             0 |    8149500 |
|  5 | mer_cal_sc_tis_20240411_20240411_4    |             0 |     940000 |
space_index.shape=(113,)
bb7_index.shape=(113,)
bb3_index.shape=(113,)
planet_index.shape=(37751,)


In [11]:
rich.inspect(ms,methods=1)

╭──────────────────────────────────── <class '__main__.MERTISSessionReader'> ─────────────────────────────────────╮
│ Class to read and process MERTIS data.                                                                          │
│                                                                                                                 │
│ ╭─────────────────────────────────────────────────────────────────────────────────────────────────────────────╮ │
│ │ <__main__.MERTISSessionReader object at 0x7f50d574d650>                                                     │ │
│ ╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────╯ │
│                                                                                                                 │
│           bb3_index = Index([    2,   211,   420,   629,   838,  1047,  1256,  1465,  1674,  1726,              │
│                              ...                                                                                │
│                              37864, 37910, 37911, 37957, 37958, 38004, 38005, 38051, 38052, 38088],             │
│                             dtype='int64', length=113)                                                          │
│           bb7_index = Index([    1,   210,   419,   628,   837,  1046,  1255,  1464,  1673,  1725,              │
│                              ...                                                                                │
│                              37862, 37908, 37909, 37955, 37956, 38002, 38003, 38049, 38050, 38087],             │
│                             dtype='int64', length=113)                                                          │
│        collect_data = {                                                                                         │
│                           'hk_default': [                                                                       │
│                               {                                                                                 │
│                                   'data':                        TIME_UTC            TIME_OBT     TimeStamp  \  │
│                       0      2024-04-11T09:01:05.938Z  1/0777546063:57998  7.775461e+08                         │
│                       1      2024-04-11T09:01:25.938Z  1/0777546083:57957  7.775461e+08                         │
│                       2      2024-04-11T09:01:45.938Z  1/0777546103:57957  7.775461e+08                         │
│                       3      2024-04-11T09:02:05.938Z  1/0777546123:57964  7.775461e+08                         │
│                       4      2024-04-11T09:02:25.938Z  1/0777546143:57954  7.775461e+08                         │
│                       ...                         ...                 ...           ...                         │
│                       28048  2024-04-11T17:15:22.468Z  1/0777575720:27136  7.775757e+08                         │
│                       28049  2024-04-11T17:15:23.466Z  1/0777575721:27038  7.775757e+08                         │
│                       28050  2024-04-11T17:15:24.466Z  1/0777575722:27030  7.775757e+08                         │
│                       28051  2024-04-11T17:15:25.466Z  1/0777575723:27028  7.775757e+08                         │
│                       28052  2024-04-11T17:15:26.466Z  1/0777575724:27038  7.775757e+08                         │
│                                                                                                                 │
│                              HK_STAT_SID  PAD  HK_STAT_MERTIS_MODE  FixVal5  HK_STAT_EEPROM_POWER  \            │
│                       0                1    0                    2        0                     0               │
│                       1                1    0                    2        0                     0               │
│                       2                1    0         